# Import Packages and Download Player Data

In [1]:
from bs4 import BeautifulSoup
import requests
import re
import pandas as pd
import numpy as np

In [2]:
# Download 2024/2025 NBA Player Data from basketball-reference.com
url = 'https://www.basketball-reference.com/leagues/NBA_2025_per_game.html#per_game_stats'
response = requests.get(url)
soup = BeautifulSoup(response.text, "html.parser")

In [ ]:
# Preview HTML output
print(soup)

# Find and gather the applicable table sections of the webpage

In [4]:
# Search for data table headers and labels
soup.find_all('th')

[<th aria-label="Rk" class="ranker poptip center" data-stat="ranker" data-tip="Rank" scope="col">Rk</th>,
 <th aria-label="Player" class="poptip sort_default_asc center" data-stat="name_display" scope="col">Player</th>,
 <th aria-label="Age" class="poptip center" data-stat="age" data-tip="Player's age on February 1 of the season" scope="col">Age</th>,
 <th aria-label="Team" class="poptip sort_default_asc center" data-stat="team_name_abbr" scope="col">Team</th>,
 <th aria-label="Pos" class="poptip center" data-stat="pos" data-tip="Position" scope="col">Pos</th>,
 <th aria-label="G" class="poptip center" data-stat="games" data-tip="Games" scope="col">G</th>,
 <th aria-label="GS" class="poptip center" data-stat="games_started" data-tip="Games Started" scope="col">GS</th>,
 <th aria-label="MP" class="poptip hide_non_quals center" data-filter="1" data-name="" data-stat="mp_per_g" data-tip="Minutes Played" scope="col">MP</th>,
 <th aria-label="FG" class="poptip hide_non_quals center" data-fi

In [5]:
# Search for data values
soup.find_all('td')

[<td class="left" csk="Gilgeous-Alexander Shai-1" data-append-csv="gilgesh01" data-stat="name_display"><a href="/players/g/gilgesh01.html">Shai Gilgeous-Alexander</a></td>,
 <td class="right" data-stat="age">26</td>,
 <td class="left" data-stat="team_name_abbr"><a href="/teams/OKC/2025.html">OKC</a></td>,
 <td class="center" data-stat="pos">PG</td>,
 <td class="right" data-stat="games">76</td>,
 <td class="right" data-stat="games_started">76</td>,
 <td class="right" csk="34.1842105263" data-stat="mp_per_g">34.2</td>,
 <td class="right" csk="11.3157894737" data-stat="fg_per_g">11.3</td>,
 <td class="right" csk="21.7894736842" data-stat="fga_per_g"><strong>21.8</strong></td>,
 <td class="right" csk="0.5193236715" data-stat="fg_pct">.519</td>,
 <td class="right" csk="2.1447368421" data-stat="fg3_per_g">2.1</td>,
 <td class="right" csk="5.7236842105" data-stat="fg3a_per_g">5.7</td>,
 <td class="right" csk="0.3747126437" data-stat="fg3_pct">.375</td>,
 <td class="right" csk="9.1710526316" d

# Scraping the data from the website

In [6]:
# Narrow down search to collect only the entries where the scope = col, this will collect the column labels and set to variable "nba_stat_titles"
nba_stat_titles = soup.find_all('th', attrs={'scope': 'col'})

In [7]:
# Preview output
print(nba_stat_titles)

[<th aria-label="Rk" class="ranker poptip center" data-stat="ranker" data-tip="Rank" scope="col">Rk</th>, <th aria-label="Player" class="poptip sort_default_asc center" data-stat="name_display" scope="col">Player</th>, <th aria-label="Age" class="poptip center" data-stat="age" data-tip="Player's age on February 1 of the season" scope="col">Age</th>, <th aria-label="Team" class="poptip sort_default_asc center" data-stat="team_name_abbr" scope="col">Team</th>, <th aria-label="Pos" class="poptip center" data-stat="pos" data-tip="Position" scope="col">Pos</th>, <th aria-label="G" class="poptip center" data-stat="games" data-tip="Games" scope="col">G</th>, <th aria-label="GS" class="poptip center" data-stat="games_started" data-tip="Games Started" scope="col">GS</th>, <th aria-label="MP" class="poptip hide_non_quals center" data-filter="1" data-name="" data-stat="mp_per_g" data-tip="Minutes Played" scope="col">MP</th>, <th aria-label="FG" class="poptip hide_non_quals center" data-filter="1"

In [8]:
# Collect only the "text" value of each entry and set the output to variable, "set" is used here to remove duplicates
stat_label_list = set([title.text.strip() for title in nba_stat_titles])

# Preview label outputs
print(stat_label_list)

{'2P%', '3P%', 'FGA', 'FG%', 'MP', 'BLK', 'G', 'TOV', 'FG', 'TRB', 'STL', 'Awards', 'Team', 'eFG%', '3P', 'Player', 'ORB', 'GS', 'AST', 'Pos', 'PTS', '2P', 'FTA', 'DRB', 'PF', 'Age', '3PA', 'FT', '2PA', 'Rk', 'FT%'}


In [9]:
df = pd.DataFrame(columns = stat_label_list)

df

Empty DataFrame
Columns: [2P%, 3P%, FGA, FG%, MP, BLK, G, TOV, FG, TRB, STL, Awards, Team, eFG%, 3P, Player, ORB, GS, AST, Pos, PTS, 2P, FTA, DRB, PF, Age, 3PA, FT, 2PA, Rk, FT%]
Index: []

[0 rows x 31 columns]

In [10]:
# Reorder the label names to match the data from table and preview
df_reordered = df.loc[:, ['Player', 'Age', 'Team', 'Pos', 'G', 'GS', 'MP', 'FG', 'FGA', 'FG%', '3P', '3PA', '3P%', '2P', '2PA', '2P%', 'eFG%', 'FT', 'FTA', 'FT%', 'ORB', 'DRB', 'TRB', 'AST', 'STL', 'BLK', 'TOV', 'PF', 'PTS', 'Awards']]

df = df_reordered
df

Empty DataFrame
Columns: [Player, Age, Team, Pos, G, GS, MP, FG, FGA, FG%, 3P, 3PA, 3P%, 2P, 2PA, 2P%, eFG%, FT, FTA, FT%, ORB, DRB, TRB, AST, STL, BLK, TOV, PF, PTS, Awards]
Index: []

[0 rows x 30 columns]

In [11]:
# Search for the table data to insert to dataframe using "tr" elements
soup.find_all('tr')

[<tr> <th aria-label="Rk" class="ranker poptip center" data-stat="ranker" data-tip="Rank" scope="col">Rk</th> <th aria-label="Player" class="poptip sort_default_asc center" data-stat="name_display" scope="col">Player</th> <th aria-label="Age" class="poptip center" data-stat="age" data-tip="Player's age on February 1 of the season" scope="col">Age</th> <th aria-label="Team" class="poptip sort_default_asc center" data-stat="team_name_abbr" scope="col">Team</th> <th aria-label="Pos" class="poptip center" data-stat="pos" data-tip="Position" scope="col">Pos</th> <th aria-label="G" class="poptip center" data-stat="games" data-tip="Games" scope="col">G</th> <th aria-label="GS" class="poptip center" data-stat="games_started" data-tip="Games Started" scope="col">GS</th> <th aria-label="MP" class="poptip hide_non_quals center" data-filter="1" data-name="" data-stat="mp_per_g" data-tip="Minutes Played" scope="col">MP</th> <th aria-label="FG" class="poptip hide_non_quals center" data-filter="1" da

In [12]:
# Set data to variable
column_data = soup.find_all('tr')

In [13]:
#loop to find only the individual data inside the "tr" elements using the "td" element and use loop to insert data into the dataframe
for row in column_data[1:]:
    row_data = row.find_all('td')
    individual_row_data = [data.text.strip() for data in row_data]
    
    # Check if the number of elements matches the DataFrame columns
    if len(individual_row_data) == len(df.columns):
        #enter each individual row data into the dataframe from before while looping through the rows
        length = len(df)
        df.loc[length] = individual_row_data
    else:
        # Option 1: Skip rows that don't match
        print(f"Skipping row with {len(individual_row_data)} elements (expected {len(df.columns)})")

Skipping row with 0 elements (expected 30)


In [14]:
df

Player Age Team Pos   G  GS    MP    FG   FGA   FG%  \
0    Shai Gilgeous-Alexander  26  OKC  PG  76  76  34.2  11.3  21.8  .519   
1      Giannis Antetokounmpo  30  MIL  PF  67  67  34.2  11.8  19.7  .601   
2              Nikola JokiÄ  29  DEN   C  70  70  36.7  11.2  19.5  .576   
3              Luka DonÄiÄ  25  2TM  PG  50  50  35.4   9.2  20.5  .450   
4              Luka DonÄiÄ  25  DAL  PG  22  22  35.7   9.8  21.2  .464   
..                       ...  ..  ...  ..  ..  ..   ...   ...   ...   ...   
951              P.J. Tucker  39  NYK  SF   1   0   4.0   0.0   0.0         
952             Jordan Walsh  20  BOS  PF   5   0   3.0   0.0   0.2  .000   
953             Cam Whitmore  20  HOU  SF   3   0   1.7   0.0   0.7  .000   
954       Jeenathan Williams  25  HOU  SG   3   0   1.7   0.0   0.3  .000   
955           League Average                                         .455   

     ...  ORB  DRB   TRB   AST  STL  BLK  TOV   PF   PTS  \
0    ...  0.9  4.1   5.0   6.4  1.7  1.0  2.4  2.2  32.7   
1    ...  2.2  9.7  11.9   6.5  0.9  1.2  3.1  2.3  30.4   
2    ...  2.9  9.9  12.7  10.2  1.8  0.6  3.3  2.3  29.6   
3    ...  0.8  7.4   8.2   7.7  1.8  0.4  3.6  2.5  28.2   
4    ...  0.7  7.6   8.3   7.8  2.0  0.4  3.4  2.6  28.1   
..   ...  ...  ...   ...   ...  ...  ...  ...  ...   ...   
951  ...  0.0  0.0   0.0   0.0  0.0  0.0  0.0  1.0   0.0   
952  ...  0.0  0.2   0.2   0.2  0.0  0.0  0.0  0.0   0.0   
953  ...  0.0  0.3   0.3   0.0  0.0  0.0  0.0  0.0   0.0   
954  ...  0.0  0.0   0.0   0.0  0.0  0.0  0.3  0.3   0.0   
955  ...                                                   

                           Awards  
0    MVP-1,DPOY-10,CPOY-8,AS,NBA1  
1            MVP-3,DPOY-8,AS,NBA1  
2            MVP-2,CPOY-2,AS,NBA1  
3                                  
4                                  
..                            ...  
951                                
952                                
953                                
954                                
955                                

[956 rows x 30 columns]

# Cleaning data

In [15]:
# Drop row with "league average"
df = df.drop(df[df['Player'] == 'League Average'].index)

df

Player Age Team Pos   G  GS    MP    FG   FGA   FG%  \
0    Shai Gilgeous-Alexander  26  OKC  PG  76  76  34.2  11.3  21.8  .519   
1      Giannis Antetokounmpo  30  MIL  PF  67  67  34.2  11.8  19.7  .601   
2              Nikola JokiÄ  29  DEN   C  70  70  36.7  11.2  19.5  .576   
3              Luka DonÄiÄ  25  2TM  PG  50  50  35.4   9.2  20.5  .450   
4              Luka DonÄiÄ  25  DAL  PG  22  22  35.7   9.8  21.2  .464   
..                       ...  ..  ...  ..  ..  ..   ...   ...   ...   ...   
950            Reed Sheppard  20  HOU  PG   3   0   3.3   0.0   0.7  .000   
951              P.J. Tucker  39  NYK  SF   1   0   4.0   0.0   0.0         
952             Jordan Walsh  20  BOS  PF   5   0   3.0   0.0   0.2  .000   
953             Cam Whitmore  20  HOU  SF   3   0   1.7   0.0   0.7  .000   
954       Jeenathan Williams  25  HOU  SG   3   0   1.7   0.0   0.3  .000   

     ...  ORB  DRB   TRB   AST  STL  BLK  TOV   PF   PTS  \
0    ...  0.9  4.1   5.0   6.4  1.7  1.0  2.4  2.2  32.7   
1    ...  2.2  9.7  11.9   6.5  0.9  1.2  3.1  2.3  30.4   
2    ...  2.9  9.9  12.7  10.2  1.8  0.6  3.3  2.3  29.6   
3    ...  0.8  7.4   8.2   7.7  1.8  0.4  3.6  2.5  28.2   
4    ...  0.7  7.6   8.3   7.8  2.0  0.4  3.4  2.6  28.1   
..   ...  ...  ...   ...   ...  ...  ...  ...  ...   ...   
950  ...  0.0  0.3   0.3   0.3  0.7  0.3  0.3  0.3   0.0   
951  ...  0.0  0.0   0.0   0.0  0.0  0.0  0.0  1.0   0.0   
952  ...  0.0  0.2   0.2   0.2  0.0  0.0  0.0  0.0   0.0   
953  ...  0.0  0.3   0.3   0.0  0.0  0.0  0.0  0.0   0.0   
954  ...  0.0  0.0   0.0   0.0  0.0  0.0  0.3  0.3   0.0   

                           Awards  
0    MVP-1,DPOY-10,CPOY-8,AS,NBA1  
1            MVP-3,DPOY-8,AS,NBA1  
2            MVP-2,CPOY-2,AS,NBA1  
3                                  
4                                  
..                            ...  
950                                
951                                
952                                
953                                
954                                

[954 rows x 30 columns]

In [16]:
#Check for duplicates
duplicate = df[df.duplicated('Player')]
duplicate

#Leaving duplicates as they contain team specific data for players who were traded, but in some cases they should be removed or cleaned

Player Age Team Pos   G  GS    MP   FG   FGA   FG%  ...  ORB  \
4         Luka DonÄiÄ  25  DAL  PG  22  22  35.7  9.8  21.2  .464  ...  0.7   
5         Luka DonÄiÄ  25  LAL  PG  28  28  35.1  8.8  20.0  .438  ...  0.9   
17        Anthony Davis  31  LAL   C  42  42  34.3  9.5  18.0  .528  ...  2.8   
18        Anthony Davis  31  DAL  PF   9   9  29.6  7.8  16.9  .461  ...  1.7   
32         De'Aaron Fox  27  SAC  PG  45  45  37.0  9.2  19.6  .469  ...  1.0   
..                  ...  ..  ...  ..  ..  ..   ...  ...   ...   ...  ...  ...   
950       Reed Sheppard  20  HOU  PG   3   0   3.3  0.0   0.7  .000  ...  0.0   
951         P.J. Tucker  39  NYK  SF   1   0   4.0  0.0   0.0        ...  0.0   
952        Jordan Walsh  20  BOS  PF   5   0   3.0  0.0   0.2  .000  ...  0.0   
953        Cam Whitmore  20  HOU  SF   3   0   1.7  0.0   0.7  .000  ...  0.0   
954  Jeenathan Williams  25  HOU  SG   3   0   1.7  0.0   0.3  .000  ...  0.0   

     DRB   TRB  AST  STL  BLK  TOV   PF   PTS Awards  
4    7.6   8.3  7.8  2.0  0.4  3.4  2.6  28.1         
5    7.2   8.1  7.5  1.6  0.4  3.7  2.4  28.2         
17   9.0  11.9  3.4  1.3  2.1  2.2  2.0  25.7         
18   8.4  10.1  4.4  0.6  2.2  2.2  1.8  20.0         
32   4.0   5.0  6.1  1.5  0.4  3.0  2.6  25.0         
..   ...   ...  ...  ...  ...  ...  ...   ...    ...  
950  0.3   0.3  0.3  0.7  0.3  0.3  0.3   0.0         
951  0.0   0.0  0.0  0.0  0.0  0.0  1.0   0.0         
952  0.2   0.2  0.2  0.0  0.0  0.0  0.0   0.0         
953  0.3   0.3  0.0  0.0  0.0  0.0  0.0   0.0         
954  0.0   0.0  0.0  0.0  0.0  0.3  0.3   0.0         

[385 rows x 30 columns]

In [17]:
# Show all columns
pd.set_option('display.max_columns', None)

# Show all rows
pd.set_option('display.max_rows', None)

# Prevent column width cutoff
pd.set_option('display.max_colwidth', None)

pd.set_option('display.width', None)

In [18]:
#Use Fuzz to fix incorrectly formatted names
target_players = ['Nikola JokiÄ', 'Luka DonÄiÄ', 'Kristaps PorziÅÄ£is', 'Alperen ÅengÃ¼n', 'Nikola VuÄeviÄ', 'Dennis SchrÃ¶der', 'Bogdan BogdanoviÄ', 'Jonas ValanÄiÅ«nas', 'Nikola JoviÄ', 'Jusuf NurkiÄ', 'Vasilije MiciÄ', 'Karlo MatkoviÄ', 'Lester QuiÃ±ones', 'Tidjane SalaÃ¼n', 'Moussa DiabatÃ©', 'Dario Å ariÄ', 'Armel TraorÃ©', 'Skal LabissiÃ¨re', 'Vlatko ÄanÄar']
valid_players = ['Nikola Jokic', 'Luka Doncic', 'Kristaps Porzingis', 'Alperen Sengun', 'Nikola Vucevic', 'Dennis Schroder', 'Bogdan Bogdanovic', 'Jonas Valanciunas', 'Nikola Jovic', 'Jusuf Nurkic', 'Vasilije Micic', 'Karlo Matkovic', 'Lester Quinones', 'Tidjane Salaun', 'Moussa Diabate', 'Dario Saric', 'Armel Traore', 'Skal Labissiere', 'Vlatko Cancar']

from fuzzywuzzy import process

# Function to apply fuzzy fix
def fuzzy_fix_player(val, valid_list, threshold=85):
    match, score = process.extractOne(val, valid_list)
    return match if score >= threshold else val

# Apply fix ONLY to rows where 'player' is in target_players
df['Player'] = df['Player'].apply(
    lambda x: fuzzy_fix_player(x, valid_players) if x in target_players else x
)

In [19]:
#Fix player names where the fuzz is not working
name_mapping = {
    "Nikola Joki": "Nikola Jokic",
    "Vasilije Mici": "Vasilije Micic",
    "Dario Å": "Dario Saric"
}

# Loop through each mapping and update rows that start with the key
for start_str, new_name in name_mapping.items():
    mask = df["Player"].str.startswith(start_str, na=False)
    df.loc[mask, "Player"] = new_name

In [20]:
# Preview dataframe

df

Player Age Team Pos   G  GS    MP    FG   FGA    FG%  \
0     Shai Gilgeous-Alexander  26  OKC  PG  76  76  34.2  11.3  21.8   .519   
1       Giannis Antetokounmpo  30  MIL  PF  67  67  34.2  11.8  19.7   .601   
2                Nikola Jokic  29  DEN   C  70  70  36.7  11.2  19.5   .576   
3                 Luka Doncic  25  2TM  PG  50  50  35.4   9.2  20.5   .450   
4                 Luka Doncic  25  DAL  PG  22  22  35.7   9.8  21.2   .464   
5                 Luka Doncic  25  LAL  PG  28  28  35.1   8.8  20.0   .438   
6             Anthony Edwards  23  MIN  SG  79  79  36.3   9.1  20.4   .447   
7                Jayson Tatum  26  BOS  PF  72  72  36.4   9.2  20.3   .452   
8                Kevin Durant  36  PHO  PF  62  62  36.5   9.5  18.1   .527   
9                Tyrese Maxey  24  PHI  PG  52  52  37.7   9.2  21.0   .437   
10            Cade Cunningham  23  DET  PG  70  70  35.0   9.8  20.8   .469   
11              Jalen Brunson  28  NYK  PG  65  65  35.4   9.0  18.5   .488   
12             Paolo Banchero  22  ORL  PF  46  46  34.4   9.0  19.8   .452   
13               Devin Booker  28  PHO  SG  75  75  37.3   8.7  18.9   .461   
14                LaMelo Ball  23  CHO  PG  47  47  32.0   8.6  21.3   .405   
15             Damian Lillard  34  MIL  PG  58  58  36.1   7.7  17.1   .448   
16              Anthony Davis  31  2TM   C  51  51  33.5   9.2  17.8   .516   
17              Anthony Davis  31  LAL   C  42  42  34.3   9.5  18.0   .528   
18              Anthony Davis  31  DAL  PF   9   9  29.6   7.8  16.9   .461   
19               Kyrie Irving  32  DAL  SG  50  50  36.1   8.9  18.9   .473   
20            Zion Williamson  24  NOP  PF  30  30  28.6   9.6  16.9   .567   
21              Stephen Curry  36  GSW  PG  70  70  32.2   8.1  18.0   .448   
22               LeBron James  40  LAL  SF  70  70  34.9   9.3  18.1   .513   
23         Karl-Anthony Towns  29  NYK   C  72  72  35.0   8.9  16.9   .526   
24          Victor Wembanyama  21  SAS   C  46  46  33.2   8.9  18.6   .476   
25               Franz Wagner  23  ORL  SF  60  60  33.7   9.0  19.4   .463   
26                 Trae Young  26  ATL  PG  76  76  36.0   7.4  18.1   .411   
27           Donovan Mitchell  28  CLE  SG  71  71  31.4   8.2  18.6   .443   
28                 Cam Thomas  23  BRK  SG  25  23  31.2   8.0  18.2   .438   
29                Tyler Herro  25  MIA  SG  77  77  35.4   8.5  17.9   .472   
30                Joel Embiid  30  PHI   C  19  19  30.2   7.4  16.6   .444   
31               De'Aaron Fox  27  2TM  PG  62  62  36.1   8.7  18.8   .463   
32               De'Aaron Fox  27  SAC  PG  45  45  37.0   9.2  19.6   .469   
33               De'Aaron Fox  27  SAS  PG  17  17  34.0   7.4  16.5   .446   
34                Zach LaVine  29  2TM  SG  74  74  35.2   8.4  16.5   .511   
35                Zach LaVine  29  CHI  SF  42  42  34.1   8.6  16.9   .511   
36                Zach LaVine  29  SAC  SG  32  32  36.6   8.2  16.0   .511   
37                  Ja Morant  25  MEM  PG  50  50  30.4   8.1  17.8   .454   
38               James Harden  35  LAC  PG  79  79  35.3   6.7  16.4   .410   
39               Jaylen Brown  28  BOS  SF  63  63  34.3   8.2  17.7   .463   
40              DeMar DeRozan  35  SAC  SF  77  77  35.9   8.1  17.0   .477   
41             Brandon Ingram  27  NOP  SF  18  18  33.1   8.6  18.5   .465   
42          Jaren Jackson Jr.  25  MEM   C  74  74  29.8   8.0  16.4   .488   
43              Norman Powell  31  LAC  SG  60  60  32.6   7.6  15.8   .484   
44             Jalen Williams  23  OKC  SG  69  69  32.4   8.2  16.9   .484   
45              Kawhi Leonard  33  LAC  SF  37  37  31.9   8.4  16.8   .498   
46               Jamal Murray  27  DEN  PG  67  67  36.1   7.9  16.7   .474   
47            Trey Murphy III  24  NOP  SF  53  51  35.0   7.2  15.8   .454   
48                 RJ Barrett  24  TOR  SF  58  58  32.2   7.9  16.9   .468   
49                CJ McCollum  33  NOP  PG  56  56  32.7   7.9  17.9   .4

In [21]:
#Check for special charcters in "Players"
pattern = r'[^a-zA-Z0-9 .-]'

# Create a mask to identify rows with special characters
mask = df['Player'].str.contains(pattern, regex=True)

# Display rows that contain special characters
special_char_rows = df[mask]
special_char_rows

Player Age Team Pos   G  GS    MP   FG   FGA   FG%   3P  3PA  \
31        De'Aaron Fox  27  2TM  PG  62  62  36.1  8.7  18.8  .463  1.9  6.1   
32        De'Aaron Fox  27  SAC  PG  45  45  37.0  9.2  19.6  .469  2.0  6.4   
33        De'Aaron Fox  27  SAS  PG  17  17  34.0  7.4  16.5  .446  1.5  5.6   
88     De'Andre Hunter  27  2TM  SF  64   9  27.2  5.6  11.9  .470  2.5  6.1   
89     De'Andre Hunter  27  ATL  SF  37   4  28.8  6.1  13.3  .461  2.6  6.7   
90     De'Andre Hunter  27  CLE  SF  27   5  25.0  4.9  10.0  .485  2.2  5.2   
150   D'Angelo Russell  28  2TM  PG  58  36  25.5  4.3  11.0  .390  1.9  6.2   
151   D'Angelo Russell  28  LAL  PG  29  10  26.3  4.4  10.7  .415  1.9  5.8   
152   D'Angelo Russell  28  BRK  PG  29  26  24.7  4.1  11.3  .367  2.0  6.6   
213  De'Anthony Melton  26  GSW  SG   6   2  20.2  3.7   9.0  .407  2.2  5.8   
253        Kel'el Ware  20  MIA   C  64  36  22.2  4.0   7.3  .554  0.5  1.7   
261      Royce O'Neale  31  PHO  SF  75  22  24.5  3.2   7.6  .423  2.4  5.9   
298     Ja'Kobe Walter  20  TOR  SG  52  18  21.2  3.1   7.6  .405  1.3  3.6   
325     Day'Ron Sharpe  23  BRK   C  50   2  18.1  3.3   6.3  .521  0.2  0.9   
354    Nae'Qwan Tomlin  24  CLE  PF   5   1  12.6  2.6   6.4  .406  0.4  2.0   
426       N'Faly Dante  23  HOU   C   4   0  12.8  2.5   3.3  .769  0.0  0.0   
581      Jae'Sean Tate  29  HOU  SF  52   2  11.3  1.3   2.8  .473  0.3  0.9   
808    De'Andre Hunter  27  CLE  SF   8   0  23.1  3.4   7.9  .429  1.5  3.3   
855        Kel'el Ware  20  MIA   C   4   4  18.3  2.0   4.5  .444  0.8  2.8   

      3P%   2P   2PA   2P%  eFG%   FT  FTA   FT%  ORB  DRB  TRB  AST  STL  \
31   .310  6.8  12.6  .538  .514  4.2  5.1  .827  0.9  3.9  4.8  6.3  1.5   
32   .322  7.2  13.3  .539  .521  4.5  5.5  .829  1.0  4.0  5.0  6.1  1.5   
33   .274  5.8  10.9  .535  .493  3.5  4.2  .819  0.5  3.8  4.3  6.8  1.5   
88   .405  3.1   5.8  .537  .573  3.4  4.0  .846  0.7  3.3  4.0  1.4  0.8   
89   .393  3.5   6.6  .531  .560  4.1  4.8  .858  0.7  3.2  3.9  1.5  0.8   
90   .426  2.6   4.8  .550  .596  2.4  2.9  .821  0.6  3.6  4.2  1.3  0.7   
150  .314  2.3   4.8  .489  .479  2.1  2.5  .834  0.3  2.4  2.8  5.1  1.0   
151  .333  2.5   4.9  .510  .505  1.6  1.8  .849  0.3  2.5  2.8  4.7  0.8   
152  .297  2.2   4.7  .467  .454  2.6  3.2  .826  0.4  2.4  2.8  5.6  1.1   
213  .371  1.5   3.2  .474  .528  0.8  1.3  .625  1.0  2.3  3.3  2.8  1.2   
253  .315  3.5   5.5  .629  .592  0.7  1.0  .687  1.8  5.6  7.4  0.9  0.6   
261  .406  0.8   1.7  .481  .580  0.3  0.3  .731  0.7  3.9  4.7  2.2  0.9   
298  .349  1.8   4.0  .454  .487  1.3  1.6  .795  1.1  1.9  3.1  1.6  0.8   
325  .244  3.1   5.4  .566  .538  1.1  1.5  .757  3.0  3.6  6.6  1.8  0.8   
354  .200  2.2   4.4  .500  .438  1.6  2.2  .727  1.8  2.4  4.2  0.4  0.0   
426        2.5   3.3  .769  .769  1.0  1.3  .800  1.5  3.8  5.3  0.5  0.3   
581  .348  1.0   2.0  .529  .527  0.6  0.9  .681  1.0  1.3  2.3  0.9  0.5   
808  .462  1.9   4.6  .405  .524  2.8  3.3  .846  0.8  2.9  3.6  1.0  0.5   
855  .273  1.3   1.8  .714  .528  0.0  0.0        1.0  3.8  4.8  1.0  0.3   

     BLK  TOV   PF   PTS  Awards  
31   0.4  2.8  2.6  23.5          
32   0.4  3.0  2.6  25.0          
33   0.3  2.4  2.7  19.7          
88   0.2  1.3  2.4  17.0  6MOY-4  
89   0.1  1.6  2.4  19.0          
90   0.3  0.9  2.5  14.3          
150  0.4  1.9  2.0  12.6          
151  0.1  1.7  1.8  12.4          
152  0.7  2.0  2.1  12.9          
213  0.3  1.7  3.0  10.3          
253  1.1  0.9  1.7   9.3   ROY-6  
261  0.5  0.9  2.0   9.1          
298  0.2  1.0  1.8   8.6          
325  0.8  1.3  2.3   7.9          
354  0.2  0.4  1.8   7.2          
426  1.3  0.5  2.3   6.0          
581  0.1  0.4  1.6   3.6          
808  0.1  0.9  2.1  11.0          
855  0.5  0.5  0.8   4.8

In [22]:
#Fill empty entries with NaN(Null) values
df.replace(r'^\s*$', np.nan, regex=True, inplace=True)

#Remove "Awards" column
df = df.drop(columns=['Awards'])

In [23]:
# Preview Dataframe
df

Player Age Team Pos   G  GS    MP    FG   FGA    FG%  \
0     Shai Gilgeous-Alexander  26  OKC  PG  76  76  34.2  11.3  21.8   .519   
1       Giannis Antetokounmpo  30  MIL  PF  67  67  34.2  11.8  19.7   .601   
2                Nikola Jokic  29  DEN   C  70  70  36.7  11.2  19.5   .576   
3                 Luka Doncic  25  2TM  PG  50  50  35.4   9.2  20.5   .450   
4                 Luka Doncic  25  DAL  PG  22  22  35.7   9.8  21.2   .464   
5                 Luka Doncic  25  LAL  PG  28  28  35.1   8.8  20.0   .438   
6             Anthony Edwards  23  MIN  SG  79  79  36.3   9.1  20.4   .447   
7                Jayson Tatum  26  BOS  PF  72  72  36.4   9.2  20.3   .452   
8                Kevin Durant  36  PHO  PF  62  62  36.5   9.5  18.1   .527   
9                Tyrese Maxey  24  PHI  PG  52  52  37.7   9.2  21.0   .437   
10            Cade Cunningham  23  DET  PG  70  70  35.0   9.8  20.8   .469   
11              Jalen Brunson  28  NYK  PG  65  65  35.4   9.0  18.5   .488   
12             Paolo Banchero  22  ORL  PF  46  46  34.4   9.0  19.8   .452   
13               Devin Booker  28  PHO  SG  75  75  37.3   8.7  18.9   .461   
14                LaMelo Ball  23  CHO  PG  47  47  32.0   8.6  21.3   .405   
15             Damian Lillard  34  MIL  PG  58  58  36.1   7.7  17.1   .448   
16              Anthony Davis  31  2TM   C  51  51  33.5   9.2  17.8   .516   
17              Anthony Davis  31  LAL   C  42  42  34.3   9.5  18.0   .528   
18              Anthony Davis  31  DAL  PF   9   9  29.6   7.8  16.9   .461   
19               Kyrie Irving  32  DAL  SG  50  50  36.1   8.9  18.9   .473   
20            Zion Williamson  24  NOP  PF  30  30  28.6   9.6  16.9   .567   
21              Stephen Curry  36  GSW  PG  70  70  32.2   8.1  18.0   .448   
22               LeBron James  40  LAL  SF  70  70  34.9   9.3  18.1   .513   
23         Karl-Anthony Towns  29  NYK   C  72  72  35.0   8.9  16.9   .526   
24          Victor Wembanyama  21  SAS   C  46  46  33.2   8.9  18.6   .476   
25               Franz Wagner  23  ORL  SF  60  60  33.7   9.0  19.4   .463   
26                 Trae Young  26  ATL  PG  76  76  36.0   7.4  18.1   .411   
27           Donovan Mitchell  28  CLE  SG  71  71  31.4   8.2  18.6   .443   
28                 Cam Thomas  23  BRK  SG  25  23  31.2   8.0  18.2   .438   
29                Tyler Herro  25  MIA  SG  77  77  35.4   8.5  17.9   .472   
30                Joel Embiid  30  PHI   C  19  19  30.2   7.4  16.6   .444   
31               De'Aaron Fox  27  2TM  PG  62  62  36.1   8.7  18.8   .463   
32               De'Aaron Fox  27  SAC  PG  45  45  37.0   9.2  19.6   .469   
33               De'Aaron Fox  27  SAS  PG  17  17  34.0   7.4  16.5   .446   
34                Zach LaVine  29  2TM  SG  74  74  35.2   8.4  16.5   .511   
35                Zach LaVine  29  CHI  SF  42  42  34.1   8.6  16.9   .511   
36                Zach LaVine  29  SAC  SG  32  32  36.6   8.2  16.0   .511   
37                  Ja Morant  25  MEM  PG  50  50  30.4   8.1  17.8   .454   
38               James Harden  35  LAC  PG  79  79  35.3   6.7  16.4   .410   
39               Jaylen Brown  28  BOS  SF  63  63  34.3   8.2  17.7   .463   
40              DeMar DeRozan  35  SAC  SF  77  77  35.9   8.1  17.0   .477   
41             Brandon Ingram  27  NOP  SF  18  18  33.1   8.6  18.5   .465   
42          Jaren Jackson Jr.  25  MEM   C  74  74  29.8   8.0  16.4   .488   
43              Norman Powell  31  LAC  SG  60  60  32.6   7.6  15.8   .484   
44             Jalen Williams  23  OKC  SG  69  69  32.4   8.2  16.9   .484   
45              Kawhi Leonard  33  LAC  SF  37  37  31.9   8.4  16.8   .498   
46               Jamal Murray  27  DEN  PG  67  67  36.1   7.9  16.7   .474   
47            Trey Murphy III  24  NOP  SF  53  51  35.0   7.2  15.8   .454   
48                 RJ Barrett  24  TOR  SF  58  58  32.2   7.9  16.9   .468   
49                CJ McCollum  33  NOP  PG  56  56  32.7   7.9  17.9   .4

In [24]:
#Check df datatypes
print(df.dtypes)

Player    object
Age       object
Team      object
Pos       object
G         object
GS        object
MP        object
FG        object
FGA       object
FG%       object
3P        object
3PA       object
3P%       object
2P        object
2PA       object
2P%       object
eFG%      object
FT        object
FTA       object
FT%       object
ORB       object
DRB       object
TRB       object
AST       object
STL       object
BLK       object
TOV       object
PF        object
PTS       object
dtype: object


In [25]:
#correct the df datatypes
df = df.astype({
    'Player': 'object',
    'Age': 'int',
    'Team': 'object',
    'Pos': 'object',
    'G': 'int',
    'GS': 'int',
    'MP': 'float64',
    'FG': 'float64',
    'FGA': 'float64',
    'FG%': 'float64',
    '3P': 'float64',
    '3PA': 'float64',
    '3P%': 'float64',
    '2P': 'float64',
    '2PA': 'float64',
    '2P%': 'float64',
    'eFG%': 'float64',
    'FT': 'float64',
    'FTA': 'float64',
    'FT%': 'float64',
    'ORB': 'float64',
    'DRB': 'float64',
    'TRB': 'float64',
    'AST': 'float64',
    'STL': 'float64',
    'BLK': 'float64',
    'TOV': 'float64',
    'PF': 'float64',
    'PTS': 'float64'
})

In [26]:
#Check df datatypes
print(df.dtypes)

Player     object
Age         int64
Team       object
Pos        object
G           int64
GS          int64
MP        float64
FG        float64
FGA       float64
FG%       float64
3P        float64
3PA       float64
3P%       float64
2P        float64
2PA       float64
2P%       float64
eFG%      float64
FT        float64
FTA       float64
FT%       float64
ORB       float64
DRB       float64
TRB       float64
AST       float64
STL       float64
BLK       float64
TOV       float64
PF        float64
PTS       float64
dtype: object


# Data Manipulation

In [27]:
# Preview Datadframe

df.head()

Player  Age Team Pos   G  GS    MP    FG   FGA    FG%  \
0  Shai Gilgeous-Alexander   26  OKC  PG  76  76  34.2  11.3  21.8  0.519   
1    Giannis Antetokounmpo   30  MIL  PF  67  67  34.2  11.8  19.7  0.601   
2             Nikola Jokic   29  DEN   C  70  70  36.7  11.2  19.5  0.576   
3              Luka Doncic   25  2TM  PG  50  50  35.4   9.2  20.5  0.450   
4              Luka Doncic   25  DAL  PG  22  22  35.7   9.8  21.2  0.464   

    3P  3PA    3P%    2P   2PA    2P%   eFG%   FT   FTA    FT%  ORB  DRB  \
0  2.1  5.7  0.375   9.2  16.1  0.571  0.569  7.9   8.8  0.898  0.9  4.1   
1  0.2  0.9  0.222  11.6  18.7  0.620  0.607  6.5  10.6  0.617  2.2  9.7   
2  2.0  4.7  0.417   9.3  14.8  0.627  0.627  5.2   6.4  0.800  2.9  9.9   
3  3.5  9.6  0.368   5.7  10.9  0.522  0.536  6.2   7.9  0.782  0.8  7.4   
4  3.4  9.6  0.354   6.4  11.5  0.555  0.544  5.1   6.6  0.767  0.7  7.6   

    TRB   AST  STL  BLK  TOV   PF   PTS  
0   5.0   6.4  1.7  1.0  2.4  2.2  32.7  
1  11.9   6.5  0.9  1.2  3.1  2.3  30.4  
2  12.7  10.2  1.8  0.6  3.3  2.3  29.6  
3   8.2   7.7  1.8  0.4  3.6  2.5  28.2  
4   8.3   7.8  2.0  0.4  3.4  2.6  28.1

In [28]:
#Create Total columns, and round to zero decimals
#use .astype() to to assign new columns as integer

df = df.assign(
    total_PTS = (df['PTS'] * df['G']).round(0).astype(int),
    total_RBS = (df['TRB'] * df['G']).round(0).astype(int),
    total_AST = (df['AST'] * df['G']).round(0).astype(int),
    total_MP = (df['MP'] * df['G']).round(0).astype(int),
    total_BLK = (df['BLK'] * df['G']).round(0).astype(int),
    total_STL = (df['STL'] * df['G']).round(0).astype(int),
    total_3PT = (df['3P'] * df['G']).round(0).astype(int),
    total_2P = (df['2P'] * df['G']).round(0).astype(int)
)

df.head()

Player  Age Team Pos   G  GS    MP    FG   FGA    FG%  \
0  Shai Gilgeous-Alexander   26  OKC  PG  76  76  34.2  11.3  21.8  0.519   
1    Giannis Antetokounmpo   30  MIL  PF  67  67  34.2  11.8  19.7  0.601   
2             Nikola Jokic   29  DEN   C  70  70  36.7  11.2  19.5  0.576   
3              Luka Doncic   25  2TM  PG  50  50  35.4   9.2  20.5  0.450   
4              Luka Doncic   25  DAL  PG  22  22  35.7   9.8  21.2  0.464   

    3P  3PA    3P%    2P   2PA    2P%   eFG%   FT   FTA    FT%  ORB  DRB  \
0  2.1  5.7  0.375   9.2  16.1  0.571  0.569  7.9   8.8  0.898  0.9  4.1   
1  0.2  0.9  0.222  11.6  18.7  0.620  0.607  6.5  10.6  0.617  2.2  9.7   
2  2.0  4.7  0.417   9.3  14.8  0.627  0.627  5.2   6.4  0.800  2.9  9.9   
3  3.5  9.6  0.368   5.7  10.9  0.522  0.536  6.2   7.9  0.782  0.8  7.4   
4  3.4  9.6  0.354   6.4  11.5  0.555  0.544  5.1   6.6  0.767  0.7  7.6   

    TRB   AST  STL  BLK  TOV   PF   PTS  total_PTS  total_RBS  total_AST  \
0   5.0   6.4  1.7  1.0  2.4  2.2  32.7       2485        380        486   
1  11.9   6.5  0.9  1.2  3.1  2.3  30.4       2037        797        436   
2  12.7  10.2  1.8  0.6  3.3  2.3  29.6       2072        889        714   
3   8.2   7.7  1.8  0.4  3.6  2.5  28.2       1410        410        385   
4   8.3   7.8  2.0  0.4  3.4  2.6  28.1        618        183        172   

   total_MP  total_BLK  total_STL  total_3PT  total_2P  
0      2599         76        129        160       699  
1      2291         80         60         13       777  
2      2569         42        126        140       651  
3      1770         20         90        175       285  
4       785          9         44         75       141

# Export NBA player data via GitHub API or local file save

Please choose either method 1 or 2 to export data

## 1. Export via GitHub API

In [42]:
import base64

# ==== CONFIGURATION ====
#For security reasons, please enter your personal github repository information to export NBA25_output.csv

GITHUB_TOKEN = "YOUR_GITHUB_PERSONAL_ACCESS_TOKEN"  #Enter Token
OWNER = "your-username-or-org"       #Enter Github Username 
REPO = "your-repo-name"              #Enter Repository Name
BRANCH = "main"                      #Enter Branch
FILE_PATH = "NBA25_output.csv"

# Convert DataFrame to CSV string
csv_data = df.to_csv(index=False)

# ==== PREPARE API REQUEST ====
api_url = f"https://api.github.com/repos/{OWNER}/{REPO}/contents/{FILE_PATH}"
headers = {"Authorization": f"token {GITHUB_TOKEN}"}

# Check if file exists to decide between update or create
res = requests.get(api_url, headers=headers, params={"ref": BRANCH})

if res.status_code == 200:
    # File exists → update
    sha = res.json()["sha"]
    message = "Update CSV from Python script"
    payload = {
        "message": message,
        "branch": BRANCH,
        "content": base64.b64encode(csv_data.encode()).decode(),
        "sha": sha
    }
    r = requests.put(api_url, headers=headers, json=payload)

elif res.status_code == 404:
    # File does not exist → create
    message = "Add CSV from Python script"
    payload = {
        "message": message,
        "branch": BRANCH,
        "content": base64.b64encode(csv_data.encode()).decode()
    }
    r = requests.put(api_url, headers=headers, json=payload)

else:
    raise Exception(f"Error checking file: {res.status_code}, {res.text}")

# ==== RESULT ====
if r.status_code in (200, 201):
    print(f"✅ CSV uploaded to GitHub at {FILE_PATH}")
else:
    print(f"❌ Error: {r.status_code}, {r.text}")

✅ CSV uploaded to GitHub at NBA25_output.csv


## 2. Export via local file save

In [ ]:
# Enter path to desired file download location
df.to_csv('{ENTER_PATH_TO_FOLDER}/NBA25_output.csv', index=False)